In [7]:
#Bokeh plotting
from bokeh.io import push_notebook, show, output_notebook
from bokeh.plotting import figure
from bokeh.models import Span, Label, Arrow, NormalHead
from bokeh.models import HoverTool, tools, ColumnDataSource, CustomJS, Slider, BoxAnnotation
from bokeh.layouts import  column, row
from bokeh.palettes import Category20_18
import re
import glob, os
from astropy.io import fits
from urllib import urlretrieve
from pyraf import iraf
output_notebook()

Loading BokehJS ...

In [8]:
with open('../listA0.txt','r') as f:
    for lines in f:
        star = lines.split(',')[0]
        url= lines.split(',')[1]
        name = url.split('/')[-1]
        if not os.path.isfile(name.strip()):
            urlretrieve(url,name.strip())
        #print(url)

In [9]:
! wc -l ../listA0.txt

100 ../listA0.txt


# Bokeh Plotting

In category can choose to plot the model or the flux. 

In [10]:
def plottingbokek(spectratoplot,limitplot,category = 'model'):

    #plot parameters
    colors = 100*Category20_18 #+ Viridis8 + Dark2_8 + Paired8 + Set1_4

    xr = (5000,8900)
    yr = (0,40)
    p =  figure(x_axis_label='Angstrom', y_axis_label='Y',title="Click on the desired stellar template to overplot", x_range=xr, y_range=yr
                  ,active_drag='pan', active_scroll='wheel_zoom',
                  plot_width=900, plot_height=1000
                 )

    hover2 = HoverTool(
            tooltips=[
                ("(x,y)", "($x{1}, $y)"),
            ]
        )
    p.add_tools(hover2)


    for index,file in enumerate(spectratoplot):

        if index < limitplot:

            ob = fits.open(file)
            dataob = ob[1].data

            x=10**(dataob['loglam'])
            y=dataob[category]

            t = p.line(x=x,y=y,color=colors[index], line_alpha=1.0, 
                   line_width=4,legend=ob[2].data['SUBCLASS'][0]+str(index),muted_alpha=0.,muted_color=colors[index])


    p.legend.location = "top_left"
    p.legend.click_policy="mute"
    show(p)

In [11]:
spectratoplot = sorted(glob.glob("spec*.fits"))
limitplot = 10
plottingbokek(spectratoplot,limitplot,category = 'flux')

## Plotting the model

In [12]:
spectratoplot = sorted(glob.glob("spec*.fits"))
limitplot = 10
plottingbokek(spectratoplot,limitplot,category = 'model')

# Table to IRAF 

To find a gaussian can use the iraf routine [fitprofs](http://stsdas.stsci.edu/cgi-bin/gethelp.cgi?fitprofs). To use this need to convert the SDSS tables to IRAF image spectra. 

In [13]:
#Parametest for the fit:
def find_nearest(array,value):
    idx = (np.abs(array-value)).argmin()
    return idx, array[idx]

def isDigit(x):
    try:
        float(x)
        return True
    except ValueError:
        return False
    
def gaussian(x, mu, sig,core):
    return core*np.exp(-np.power(x - mu, 2.) / (2 * np.power(sig, 2.)))

#Emission Lines
class line(object):
    def __init__(self,name,linecenter,regiontofit):
        self.name = name
        self.linecenter = linecenter
        self.regiontofit = regiontofit
        


def fitlinesspectra(listspectra, dicoflines, limit, plotting ,eeqwgs,linesdicall,errorestimate,errorparam):

    
    if plotting == True:
    
        #plot parameters
        colors = 100*Category20_18 #+ Viridis8 + Dark2_8 + Paired8 + Set1_4
        xr = (5000,8900)
        yr = (0,40)
        pl =  figure(x_axis_label='Angstrom', y_axis_label='Y',title="Click on the desired stellar template to overplot", x_range=xr, y_range=yr
                      ,active_drag='pan', active_scroll='wheel_zoom',
                      plot_width=900, plot_height=1000
                     )

        hover2 = HoverTool(
                tooltips=[
                    ("(x,y)", "($x{1}, $y)"),
                ]
            )
        pl.add_tools(hover2)
    
    

    ##Looping all the .fits file
    for index,filename in enumerate(listspectra):
        
        filenameoriginal = filename
        #Maximiin number of spectra to fit
        if index < limit:
            #import fits
            ob = fits.open(filename)
            #Get data and save wavelenft in x, and flux on y
            dataob = ob[1].data
            x = 10**(dataob['loglam'])
            y = dataob['model']

            #save to a .txt file
            namenewfits = '{name}.txt'.format(name=filename.split('.')[0])
            with open(namenewfits,'w') as file:
                for i in zip(x,y):
                    file.write('{}\t{}\n'.format(i[0],i[1]))
            #Create fits file from text file interpolation to work wtih IRAF functions
            iraffitsname = 'iraf'+filename.split('.')[0]
            if os.path.exists(iraffitsname+'.fits'):
                os.remove(iraffitsname+'.fits')

            iraf.noao.onedspec()
            iraf.dataio()
            iraf.rspectext(namenewfits,iraffitsname,dtype='interp')

            #Initialize files log and lines
            ! echo '' > fited.log



            for indexline,linesfit in enumerate(dicoflines):
                regionf = "{} {}".format(linesfit.regiontofit[0],linesfit.regiontofit[1])
                #wavelenght
                xlimns = [find_nearest(x,i)[0] for i in linesfit.regiontofit   ]
                wavex = x[xlimns[0]:xlimns[1]]
                lineszero = linesfit.linecenter
                ! echo '$lineszero' > lines.lines

                filename = iraffitsname
                #Error estimation iraf: http://stsdas.stsci.edu/cgi-bin/gethelp.cgi?fitprofs
                if errorestimate == True:        
                    iraf.fitprofs(filename,pos='lines.lines', reg=regionf ,
                                  fitbackground= 'yes', 
                                  logfile='fited.log'
                                  ,nerrsample='100',sigma0='4',invgain='4')
                else:
                    iraf.fitprofs(filename,pos='lines.lines', reg=regionf ,
                                  fitbackground= 'yes', 
                                  logfile='fited.log')



                #Plotting the gaussian
                #Find in log file of fitprofs.  
                npattern = re.compile('[-\d.]+')
                npattern2 = re.compile('[-\d.E?]+') #Gets the exponentioals

                gparameters=[]
                with open('fited.log','r') as file:
                    for lines in file:

                        if '(' not in lines:
                            temp = npattern2.findall(lines)
                            if 'INDEF' in lines:
                                gparameters.append(7*[0])
                        else:
                            errorparam.append(npattern2.findall(lines))

                        if len(temp) == 7 and all(isDigit(i) for i in temp) and 'INDEF' not in lines:
                            gparameters.append(temp)

                #gaussian
                if len(gparameters) > 0:
                    gparamfinal = [ float(i) for i in gparameters[-1] ]
                    centerg, contg, fluxg, eqwg, coreg, fwhmg, fwhml = gparamfinal
                    yg = gaussian(wavex,centerg,fwhmg/2.3538,coreg) + contg


                if errorestimate == True:
                    errorparamfinal = [ float(i) for i in errorparam[-1] ]
                    print(gparamfinal)
                    print(errorparamfinal)


                    linesdic = {'name':ob[2].data['SUBCLASS'][0]+str(index),
                                 'linename':linesfit.name,
                                 'center':centerg,
                                  'EW': eqwg,
                                  'EWerror':errorparamfinal[3],
                                'fluxg':fluxg,
                                'coreg':coreg,
                                'fwgmg':fwhmg,
                                'contg':contg,
                                'filename':filenameoriginal
                                }
                    linesdicall.append(linesdic)

                    message = 'Name:{sclass},center:{cent},eqw:{eq}({eqer})'


                    eeqwgs.append([message.format(
                        sclass = ob[2].data['SUBCLASS'][0]+str(index),
                        cent = centerg
                        ,eq = eqwg
                        ,eqer = errorparamfinal[3])])


                    if plotting == True:
                        

                        pl.line(wavex,yg,color='red', line_alpha=1.,
                                line_width=5,legend=ob[2].data['SUBCLASS'][0]+str(index),muted_alpha=0.,muted_color=colors[index])



                        #If you want to have the name and not the spectra type change legend=name
                        t = pl.line(x=x,y=y,color=colors[index], line_alpha=1.0, 
                                    line_width=4,legend=ob[2].data['SUBCLASS'][0]+str(index),muted_alpha=0.,muted_color=colors[index])


    if plotting == True:
    
        pl.legend.location = "top_left"
        pl.legend.click_policy="mute"

        show(pl)           

In [15]:
eeqwgs = [] #List of messages
linesdicall =[] # Diccionary of all the fitted lines
errorparam = []  # The error per fittted line
errorestimate = True  # Estimate or no estimate error based on iraf
plotting = True  #If plot the spectra and the fitted gaussians
limitfit = 3   # Limit fo the first # of spectra to fit and plot if plottting=True

##Defines the lines to try to fit. The name, center of the line, region used to do the fitting. 
diclines = {line('P15',8547,[8520,8560]),line('P14',8600,[8600-20,8600+20]),
           line('Halpha',6562,[6550,6575]),line('P16',8504,[8504-20,8504+20]),
            line('P13',8667,[8667-20,8667+20]),line('P12',8752,[8752-20,8752+20]),
           line('P11',8865,[8865-20,8865+20]),line('P10',9017,[9017-20,9017+20])}
                    
listofspectratofit = sorted(glob.glob("spec*.fits"));  #List of spectra to fit. Sorted all spec by default

#Call the function with the above parameters
fitlinesspectra(listofspectratofit,diclines,limitfit,plotting,eeqwgs,linesdicall,errorestimate,errorparam)

# Feb  2 14:01 irafspec-0266-51630-0015 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center      cont      flux       eqw      core     gfwhm     lfwhm
  8757.704  9.671695  -15.1684     1.568  -1.04753      13.6        0.
 (42.7734) (3.00002) ( 1046.2) (  13.02) (25.9032) (  54.83) (     0.)
[8757.704, 9.671695, -15.1684, 1.568, -1.04753, 13.6, 0.0]
[42.7734, 3.00002, 1046.2, 13.02, 25.9032, 54.83, 0.0]
# Feb  2 14:01 irafspec-0266-51630-0015 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center      cont      flux       eqw      core     gfwhm     lfwhm
   8507.54  9.961484  -4.56159    0.4579 -0.471568     9.087        0.
 (169.432) (2.48729) (2139.23) (  64.02) ( 30.032) (  62.44) (     0.)
[8507.54, 9.961484, -4.56159, 0.4579, -0.471568, 9.087, 0.0]
[169.432, 2.48729, 2139.23, 64.02, 30.032, 62.44, 0.0]
# Feb  2 14:01 irafspec-0266-51630-0015 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center 

[9021.274, 20.91498, -80.1434, 3.832, -5.31167, 14.17, 0.0]
[8.39063, 3.76662, 182.805, 5.926, 14.4911, 14.13, 0.0]
# Feb  2 14:01 irafspec-0266-51630-0140 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center      cont      flux       eqw      core     gfwhm     lfwhm
  8669.937  23.05209  -37.2542     1.616  -4.69681     7.451        0.
 (7.62012) ( 3.4158) (136.305) (  4.602) (21.8926) (  10.56) (     0.)
[8669.937, 23.05209, -37.2542, 1.616, -4.69681, 7.451, 0.0]
[7.62012, 3.4158, 136.305, 4.602, 21.8926, 10.56, 0.0]
# Feb  2 14:01 irafspec-0266-51630-0140 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center      cont      flux       eqw      core     gfwhm     lfwhm
  8550.337  23.51293  -37.2116     1.583  -3.85517     9.068        0.
 (17.9297) (3.73056) (190.309) (  5.729) (21.3586) (  8.409) (     0.)
[8550.337, 23.51293, -37.2116, 1.583, -3.85517, 9.068, 0.0]
[17.9297, 3.73056, 190.309, 5.729, 21.3586, 8.409, 0.0]
# Feb

# Plotting some

In [19]:
set([ (i['center'],i['EWerror']) for i in linesdicall if i['linename'] =='Halpha' ])

{(6566.081, 28.41), (6567.792, 3.021), (6568.445, 16.44)}

In [18]:
listatry = set([ i['filename'] for i in linesdicall if i['EWerror'] < 200])
plottingbokek(listatry,len(listatry))

# Fitting many spectra

In [ ]:
eeqwgs = [] #List of messages
linesdicall =[] # Diccionary of all the fitted lines
errorparam = []  # The error per fittted line
errorestimate = True  # Estimate or no estimate error based on iraf
plotting = False  #If plot the spectra and the fitted gaussians
limitfit = 10   # Limit fo the first # of spectra to fit and plot if plottting=True

##Defines the lines to try to fit. The name, center of the line, region used to do the fitting. 
diclines = {line('Halpha',8543,[8520,8560]),line('P1',8598,[8582,8609]),
           line('P2',6562,[6550,6575])}
                    
listofspectratofit = sorted(glob.glob("spec*.fits"));  #List of spectra to fit. Sorted all spec by default

#Call the function with the above parameters
fitlinesspectra(listofspectratofit,diclines,limitfit,plotting,eeqwgs,linesdicall,errorestimate,errorparam)